## Data Cleansing - Staging to Silver Layer

This notebook will be used to go through each dataset and cleansing the data. This will include dealing with null values, trimming any unneeded columns, making sure that the data types matched from the schema design set for the staging level (done in previous notebook). No aggregations or calculations will be made in this silver layer.

In [0]:
display(dbutils.fs.ls("dbfs:/nfl_project/raw"))

path name size modificationTime dbfs:/nfl_project/raw/QB_2000_2020_Data.csv QB_2000_2020_Data.csv 113630 1672242319000 dbfs:/nfl_project/raw/draft_picks.csv draft_picks.csv 533702 1672242322000 dbfs:/nfl_project/raw/games.csv games.csv 1848734 1672242322000 dbfs:/nfl_project/raw/probowlers_2000_2019.csv probowlers_2000_2019.csv 228082 1672242320000 dbfs:/nfl_project/raw/rosters.csv rosters.csv 1606485 1672242321000 dbfs:/nfl_project/raw/standings.csv standings.csv 42523 1672242321000

In [0]:
display(dbutils.fs.ls("dbfs:/nfl_project/staging"))

path name size modificationTime dbfs:/nfl_project/staging/draft_picks.parquet/ draft_picks.parquet/ 0 0 dbfs:/nfl_project/staging/games_data.parquet/ games_data.parquet/ 0 0 dbfs:/nfl_project/staging/probowlers.parquet/ probowlers.parquet/ 0 0 dbfs:/nfl_project/staging/qb_stats.parquet/ qb_stats.parquet/ 0 0 dbfs:/nfl_project/staging/rosters.parquet/ rosters.parquet/ 0 0 dbfs:/nfl_project/staging/standings.parquet/ standings.parquet/ 0 0

In [0]:
qb_silver = spark.read.parquet("dbfs:/nfl_project/staging/qb_stats.parquet")
draft_picks_silver = spark.read.parquet("dbfs:/nfl_project/staging/draft_picks.parquet")
games_silver = spark.read.parquet("dbfs:/nfl_project/staging/games_data.parquet")
probowlers_silver = spark.read.parquet("dbfs:/nfl_project/staging/probowlers.parquet")
roster_silver = spark.read.parquet("dbfs:/nfl_project/staging/rosters.parquet")
standings_silver = spark.read.parquet("dbfs:/nfl_project/staging/standings.parquet")

In [0]:
import pandas as pd

In [0]:
display(qb_silver)

year qb_rank player team age position games_played games_started record completions attempts completion_perc yards TDs TD_perc interceptions int_perc first_down_passes longest_throw yards_per_attempt adj_yards_per_attempt yards_per_completion yards_per_game quarterback_rating QBR sacks yards_from_sacks net_yards_per_attempt adj_net_yards_per_attempt sack_percent fourth_qtr_comebacks game_winning_drives 2019 1 Jameis Winston TAM 25 QB 16 16 7-9-0 380 626 60.7 5109 33 5.3 30 4.8 243 71 8.2 7.1 13.4 319.3 84.3 55.7 47 282 7.17 6.15 7.0 2 2 2019 2 Dak Prescott DAL 26 QB 16 16 8-8-0 388 596 65.1 4902 30 5.0 11 1.8 229 62 8.2 8.4 12.6 306.4 99.7 71.9 23 151 7.68 7.84 3.7 null null 2019 3 Jared Goff LAR 25 QB 16 16 9-7-0 394 626 62.9 4638 22 3.5 16 2.6 220 66 7.4 7.0 11.8 289.9 86.5 50.6 22 170 6.9 6.46 3.4 1 2 2019 4 Philip Rivers LAC 38 QB 16 16 5-11-0 390 591 66.0 4615 23 3.9 20 3.4 217 84 7.8 7.1 11.8 288.4 88.5 50.5 34 222 7.03 6.32 5.4 1 2 2019 5 Matt Ryan ATL 34 QB 15 15 7-8-0 408 616 66.2 4466 26 4.2 14 2.3 228 93 7.3 7.1 10.9 297.7 92.1 59.6 48 316 6.25 6.08 7.2 3 2 2019 6 Russell Wilson* SEA 31 QB 16 16 11-5-0 341 516 66.1 4110 31 6.0 5 1.0 190 60 8.0 8.7 12.1 256.9 106.3 71.5 48 319 6.72 7.42 8.5 4 5 2019 7 Tom Brady NWE 42 QB 16 16 12-4-0 373 613 60.8 4057 24 3.9 8 1.3 193 59 6.6 6.8 10.9 253.6 88.0 55.7 27 185 6.05 6.24 4.2 1 1 2019 8 Derek Carr OAK 28 QB 16 16 7-9-0 361 513 70.4 4054 21 4.1 8 1.6 191 75 7.9 8.0 11.2 253.4 100.8 64.1 29 184 7.14 7.25 5.4 2 3 2019 9 Carson Wentz PHI 27 QB 16 16 9-7-0 388 607 63.9 4039 27 4.4 7 1.2 213 53 6.7 7.0 10.4 252.4 93.1 62.8 37 230 5.91 6.26 5.7 2 4 2019 10 Patrick Mahomes* KAN 24 QB 14 14 11-3-0 319 484 65.9 4031 26 5.4 5 1.0 176 83 8.3 8.9 12.6 287.9 105.3 77.7 17 127 7.79 8.38 3.4 1 1 2019 11 Aaron Rodgers* GNB 36 QB 16 16 13-3-0 353 569 62.0 4002 26 4.6 4 0.7 189 74 7.0 7.6 11.3 250.1 95.4 52.5 36 284 6.15 6.71 6.0 2 3 2019 12 Jimmy Garoppolo SFO 28 QB 16 16 13-3-0 329 476 69.1 3978 27 5.7 13 2.7 193 75 8.4 8.3 12.1 248.6 102.0 60.8 36 237 7.31 7.22 7.0 4 4 2019 13 Deshaun Watson* HOU 24 QB 15 15 10-5-0 333 495 67.3 3852 26 5.3 12 2.4 191 54 7.8 7.7 11.6 256.8 98.0 70.5 44 257 6.67 6.63 8.2 3 5 2019 14 Baker Mayfield CLE 24 QB 16 16 6-10-0 317 534 59.4 3827 22 4.1 21 3.9 179 89 7.2 6.2 12.1 239.2 78.8 54.4 40 285 6.17 5.29 7.0 1 1 2019 15 Kyler Murray ARI 22 QB 16 16 5-10-1 349 542 64.4 3722 20 3.7 12 2.2 173 88 6.9 6.6 10.7 232.6 87.4 57.7 48 309 5.78 5.55 8.1 1 2 2019 16 Kirk Cousins* MIN 31 QB 15 15 10-5-0 307 444 69.1 3603 26 5.9 6 1.4 165 66 8.1 8.7 11.7 240.2 107.4 60.4 28 206 7.2 7.73 5.9 1 1 2019 17 Ryan Fitzpatrick MIA 37 QB 15 13 5-8-0 311 502 62.0 3529 20 4.0 13 2.6 182 51 7.0 6.7 11.3 235.3 85.5 68.3 40 209 6.13 5.78 7.4 3 4 2019 18 Andy Dalton CIN 32 QB 13 13 2-11-0 314 528 59.5 3494 16 3.0 14 2.7 170 66 6.6 6.0 11.1 268.8 78.3 42.1 37 249 5.74 5.19 6.5 null null 2019 19 Kyle Allen CAR 23 QB 13 12 5-7-0 303 489 62.0 3322 17 3.5 16 3.3 188 52 6.8 6.0 11.0 255.5 80.0 38.3 46 397 5.47 4.76 8.6 0 1 2019 20 Gardner Minshew II JAX 23 QB 14 12 6-6-0 285 470 60.6 3271 21 4.5 6 1.3 150 70 7.0 7.3 11.5 233.6 91.2 44.6 33 184 6.14 6.44 6.6 3 3 2019 21 Mitchell Trubisky CHI 25 QB 15 15 8-7-0 326 516 63.2 3138 17 3.3 10 1.9 156 53 6.1 5.9 9.6 209.2 83.0 41.5 38 234 5.24 5.04 6.9 3 3 2019 22 Lamar Jackson*+ BAL 22 QB 15 15 13-2-0 265 401 66.1 3127 36 9.0 6 1.5 161 83 7.8 8.9 11.8 208.5 113.3 83.0 23 106 7.13 8.19 5.4 1 2 2019 23 Josh Allen BUF 23 QB 16 16 10-6-0 271 461 58.8 3089 20 4.3 9 2.0 146 53 6.7 6.7 11.4 193.1 85.3 49.4 38 237 5.72 5.71 7.6 4 5 2019 24 Daniel Jones NYG 22 QB 13 12 3-9-0 284 459 61.9 3027 24 5.2 12 2.6 140 75 6.6 6.5 10.7 232.8 87.7 55.7 38 295 5.5 5.38 7.6 1 2 2019 25 Sam Darnold NYJ 22 QB 13 13 7-6-0 273 441 61.9 3024 19 4.3 13 2.9 147 92 6.9 6.4 11.1 232.6 84.3 45.6 33 212 5.93 5.5 7.0 2 3 2019 26 Drew Brees* NOR 40 QB 11 11 8-3-0 281 378 74.3 2979 27 7.1 4 1.1 159 61 7.9 8.8 10.6 270.8 116.3 73.3 12 89 7.41 8.33 3.1 1 2 2019 27 Jacoby Brissett IND 27

In [0]:
# cleanse the * after the names - * is probowl and + is first team all pro, but that is already in the probowlers df
# get rid of the nulls from fourth qtr comebacks and game winning drives and set them to 0
# data before 2005 does not have QBR
# some QB names have slashes in them, and some have the name repeated
# some positions are in the dataframe that are not QBs - we want to filter those out

# setting up variables. Whitelist is just letters and a space. temp_qb_df is a pandas dataframe I will use to cleanse the data
whitelist = set('abcdefghijklmnopqrstuvwxyz ABCDEFGHIJKLMNOPQRSTUVWXYZ')
temp_qb_df = qb_silver.toPandas()
# dropping the row if the player or position is null
temp_qb_df = temp_qb_df.dropna(subset=['player', 'position'])
# filling null values with 0s
temp_qb_df['fourth_qtr_comebacks'] = temp_qb_df['fourth_qtr_comebacks'].fillna(0)
temp_qb_df['game_winning_drives'] = temp_qb_df['game_winning_drives'].fillna(0)

for i in temp_qb_df.index:
  # if a player has a slash in his name, get rid of it
  if "\\" in temp_qb_df.loc[i,'player']:
    t = temp_qb_df.loc[i,'player'].split("\\")[0]
    temp_qb_df.loc[i,'player'] = t
  
#   if temp_qb_df.loc[i,'player'] =="Bilal Powell":
#     print(temp_qb_df.loc[i,'position'])
#     if "/"  in temp_qb_df.loc[i,'position']:
#       print("hi there")
  # make sure there is no forward slash in the players position
  if "/" in temp_qb_df.loc[i,'position']:
    p = ''.join(filter(whitelist.__contains__, temp_qb_df.loc[i,'position']))
    #print('HI')
    temp_qb_df.loc[i,'position'] = p
  # making sure the players name is only letters or a space
  temp_qb_df.loc[i,'player'] = ''.join(filter(whitelist.__contains__, temp_qb_df.loc[i,'player']))
  # cleaning out none QBs from the passing statistics
  temp_qb_df.loc[i,'position'] = temp_qb_df.loc[i,'position'].upper()
  if temp_qb_df.loc[i,'position'] not in ["QB", "qb"]:
    temp_qb_df = temp_qb_df.drop(i)
  # making all the positions uppercase
  

qb_silver_final = temp_qb_df
display(qb_silver_final)
# this data frame will not be used going forward, the view developed below does the same thing, but is faster and more efficient

year qb_rank player team age position games_played games_started record completions attempts completion_perc yards TDs TD_perc interceptions int_perc first_down_passes longest_throw yards_per_attempt adj_yards_per_attempt yards_per_completion yards_per_game quarterback_rating QBR sacks yards_from_sacks net_yards_per_attempt adj_net_yards_per_attempt sack_percent fourth_qtr_comebacks game_winning_drives 2019.0 1.0 Jameis Winston TAM 25.0 QB 16.0 16.0 7-9-0 380.0 626.0 60.7 5109.0 33.0 5.3 30.0 4.8 243.0 71.0 8.2 7.1 13.4 319.3 84.3 55.7 47.0 282.0 7.17 6.15 7.0 2.0 2.0 2019.0 2.0 Dak Prescott DAL 26.0 QB 16.0 16.0 8-8-0 388.0 596.0 65.1 4902.0 30.0 5.0 11.0 1.8 229.0 62.0 8.2 8.4 12.6 306.4 99.7 71.9 23.0 151.0 7.68 7.84 3.7 0.0 0.0 2019.0 3.0 Jared Goff LAR 25.0 QB 16.0 16.0 9-7-0 394.0 626.0 62.9 4638.0 22.0 3.5 16.0 2.6 220.0 66.0 7.4 7.0 11.8 289.9 86.5 50.6 22.0 170.0 6.9 6.46 3.4 1.0 2.0 2019.0 4.0 Philip Rivers LAC 38.0 QB 16.0 16.0 5-11-0 390.0 591.0 66.0 4615.0 23.0 3.9 20.0 3.4 217.0 84.0 7.8 7.1 11.8 288.4 88.5 50.5 34.0 222.0 7.03 6.32 5.4 1.0 2.0 2019.0 5.0 Matt Ryan ATL 34.0 QB 15.0 15.0 7-8-0 408.0 616.0 66.2 4466.0 26.0 4.2 14.0 2.3 228.0 93.0 7.3 7.1 10.9 297.7 92.1 59.6 48.0 316.0 6.25 6.08 7.2 3.0 2.0 2019.0 6.0 Russell Wilson SEA 31.0 QB 16.0 16.0 11-5-0 341.0 516.0 66.1 4110.0 31.0 6.0 5.0 1.0 190.0 60.0 8.0 8.7 12.1 256.9 106.3 71.5 48.0 319.0 6.72 7.42 8.5 4.0 5.0 2019.0 7.0 Tom Brady NWE 42.0 QB 16.0 16.0 12-4-0 373.0 613.0 60.8 4057.0 24.0 3.9 8.0 1.3 193.0 59.0 6.6 6.8 10.9 253.6 88.0 55.7 27.0 185.0 6.05 6.24 4.2 1.0 1.0 2019.0 8.0 Derek Carr OAK 28.0 QB 16.0 16.0 7-9-0 361.0 513.0 70.4 4054.0 21.0 4.1 8.0 1.6 191.0 75.0 7.9 8.0 11.2 253.4 100.8 64.1 29.0 184.0 7.14 7.25 5.4 2.0 3.0 2019.0 9.0 Carson Wentz PHI 27.0 QB 16.0 16.0 9-7-0 388.0 607.0 63.9 4039.0 27.0 4.4 7.0 1.2 213.0 53.0 6.7 7.0 10.4 252.4 93.1 62.8 37.0 230.0 5.91 6.26 5.7 2.0 4.0 2019.0 10.0 Patrick Mahomes KAN 24.0 QB 14.0 14.0 11-3-0 319.0 484.0 65.9 4031.0 26.0 5.4 5.0 1.0 176.0 83.0 8.3 8.9 12.6 287.9 105.3 77.7 17.0 127.0 7.79 8.38 3.4 1.0 1.0 2019.0 11.0 Aaron Rodgers GNB 36.0 QB 16.0 16.0 13-3-0 353.0 569.0 62.0 4002.0 26.0 4.6 4.0 0.7 189.0 74.0 7.0 7.6 11.3 250.1 95.4 52.5 36.0 284.0 6.15 6.71 6.0 2.0 3.0 2019.0 12.0 Jimmy Garoppolo SFO 28.0 QB 16.0 16.0 13-3-0 329.0 476.0 69.1 3978.0 27.0 5.7 13.0 2.7 193.0 75.0 8.4 8.3 12.1 248.6 102.0 60.8 36.0 237.0 7.31 7.22 7.0 4.0 4.0 2019.0 13.0 Deshaun Watson HOU 24.0 QB 15.0 15.0 10-5-0 333.0 495.0 67.3 3852.0 26.0 5.3 12.0 2.4 191.0 54.0 7.8 7.7 11.6 256.8 98.0 70.5 44.0 257.0 6.67 6.63 8.2 3.0 5.0 2019.0 14.0 Baker Mayfield CLE 24.0 QB 16.0 16.0 6-10-0 317.0 534.0 59.4 3827.0 22.0 4.1 21.0 3.9 179.0 89.0 7.2 6.2 12.1 239.2 78.8 54.4 40.0 285.0 6.17 5.29 7.0 1.0 1.0 2019.0 15.0 Kyler Murray ARI 22.0 QB 16.0 16.0 5-10-1 349.0 542.0 64.4 3722.0 20.0 3.7 12.0 2.2 173.0 88.0 6.9 6.6 10.7 232.6 87.4 57.7 48.0 309.0 5.78 5.55 8.1 1.0 2.0 2019.0 16.0 Kirk Cousins MIN 31.0 QB 15.0 15.0 10-5-0 307.0 444.0 69.1 3603.0 26.0 5.9 6.0 1.4 165.0 66.0 8.1 8.7 11.7 240.2 107.4 60.4 28.0 206.0 7.2 7.73 5.9 1.0 1.0 2019.0 17.0 Ryan Fitzpatrick MIA 37.0 QB 15.0 13.0 5-8-0 311.0 502.0 62.0 3529.0 20.0 4.0 13.0 2.6 182.0 51.0 7.0 6.7 11.3 235.3 85.5 68.3 40.0 209.0 6.13 5.78 7.4 3.0 4.0 2019.0 18.0 Andy Dalton CIN 32.0 QB 13.0 13.0 2-11-0 314.0 528.0 59.5 3494.0 16.0 3.0 14.0 2.7 170.0 66.0 6.6 6.0 11.1 268.8 78.3 42.1 37.0 249.0 5.74 5.19 6.5 0.0 0.0 2019.0 19.0 Kyle Allen CAR 23.0 QB 13.0 12.0 5-7-0 303.0 489.0 62.0 3322.0 17.0 3.5 16.0 3.3 188.0 52.0 6.8 6.0 11.0 255.5 80.0 38.3 46.0 397.0 5.47 4.76 8.6 0.0 1.0 2019.0 20.0 Gardner Minshew II JAX 23.0 QB 14.0 12.0 6-6-0 285.0 470.0 60.6 3271.0 21.0 4.5 6.0 1.3 150.0 70.0 7.0 7.3 11.5 233.6 91.2 44.6 33.0 184.0 6.14 6.44 6.6 3.0 3.0 2019.0 21.0 Mitchell Trubisky CHI 25.0 QB 15.0 15.0 8-7-0 326.0 516.0 63.2 3138.0 17.0 3.3 10.0 1.9 156.0 53.0 6.1 5.9 9.6 209.2 83.0 41.5 38.0 234.0 5.24 5.04 6.9 3.0 3.0 2019.0 22.0 Lamar Jackson BAL 22.0 QB 15.0 15.0 13-2

In [0]:
qb_silver.createOrReplaceTempView("qb_silver_temp")

In [0]:
qb_silver_post_2005 = spark.sql("""
SELECT  
  year
, qb_rank
, (case
    when CHARINDEX("*", player) > 0 then
        left(player, CHARINDEX("*", player) - 1)
    when CHARINDEX("+", player) > 0 then
        left(player, CHARINDEX("+", player) - 1)
    when CHARINDEX("\\\\", player) > 0 then
        left(player, CHARINDEX("\\\\", player) - 1)
    else
        player
  end) as player
, (case when team = "TAM" then "TB"
      when team = "GNB" then "GB"
      when team = "KAN" then "KC"
      when team = "LVR" then "LV"
      when team = "NOR" then "NO"
      when team = "NWE" then "NE"
      when team = "SDG" then "SD"
      when team = "SFO" then "SF"
      else team
  end) as team
, age
, (case         
    when CHARINDEX('Q', position) > 0 then
        'QB'
    when CHARINDEX('q', position) > 0 then
        'QB'
    else
        'non-QB'
    end) as position
, games_played
, games_started
, record
, completions
, attempts
, completion_perc
, yards
, TDs
, TD_perc
, interceptions
, int_perc
, first_down_passes
, longest_throw
, yards_per_attempt
, adj_yards_per_attempt
, yards_per_completion
, yards_per_game
, quarterback_rating
, QBR
, sacks
, yards_from_sacks
, net_yards_per_attempt
, adj_net_yards_per_attempt
, sack_percent
, COALESCE(fourth_qtr_comebacks, 0) as fourth_qtr_comebacks
, COALESCE(game_winning_drives, 0) as game_winning_drives

FROM qb_silver_temp
WHERE player is not null and position is not null 
and (position LIKE '%QB%' or position LIKE '%qb%')
AND year > 2005 """)

In [0]:
display(qb_silver_post_2005)

year qb_rank player team age position games_played games_started record completions attempts completion_perc yards TDs TD_perc interceptions int_perc first_down_passes longest_throw yards_per_attempt adj_yards_per_attempt yards_per_completion yards_per_game quarterback_rating QBR sacks yards_from_sacks net_yards_per_attempt adj_net_yards_per_attempt sack_percent fourth_qtr_comebacks game_winning_drives 2019 1 Jameis Winston TB 25 QB 16 16 7-9-0 380 626 60.7 5109 33 5.3 30 4.8 243 71 8.2 7.1 13.4 319.3 84.3 55.7 47 282 7.17 6.15 7.0 2 2 2019 2 Dak Prescott DAL 26 QB 16 16 8-8-0 388 596 65.1 4902 30 5.0 11 1.8 229 62 8.2 8.4 12.6 306.4 99.7 71.9 23 151 7.68 7.84 3.7 0 0 2019 3 Jared Goff LAR 25 QB 16 16 9-7-0 394 626 62.9 4638 22 3.5 16 2.6 220 66 7.4 7.0 11.8 289.9 86.5 50.6 22 170 6.9 6.46 3.4 1 2 2019 4 Philip Rivers LAC 38 QB 16 16 5-11-0 390 591 66.0 4615 23 3.9 20 3.4 217 84 7.8 7.1 11.8 288.4 88.5 50.5 34 222 7.03 6.32 5.4 1 2 2019 5 Matt Ryan ATL 34 QB 15 15 7-8-0 408 616 66.2 4466 26 4.2 14 2.3 228 93 7.3 7.1 10.9 297.7 92.1 59.6 48 316 6.25 6.08 7.2 3 2 2019 6 Russell Wilson SEA 31 QB 16 16 11-5-0 341 516 66.1 4110 31 6.0 5 1.0 190 60 8.0 8.7 12.1 256.9 106.3 71.5 48 319 6.72 7.42 8.5 4 5 2019 7 Tom Brady NE 42 QB 16 16 12-4-0 373 613 60.8 4057 24 3.9 8 1.3 193 59 6.6 6.8 10.9 253.6 88.0 55.7 27 185 6.05 6.24 4.2 1 1 2019 8 Derek Carr OAK 28 QB 16 16 7-9-0 361 513 70.4 4054 21 4.1 8 1.6 191 75 7.9 8.0 11.2 253.4 100.8 64.1 29 184 7.14 7.25 5.4 2 3 2019 9 Carson Wentz PHI 27 QB 16 16 9-7-0 388 607 63.9 4039 27 4.4 7 1.2 213 53 6.7 7.0 10.4 252.4 93.1 62.8 37 230 5.91 6.26 5.7 2 4 2019 10 Patrick Mahomes KC 24 QB 14 14 11-3-0 319 484 65.9 4031 26 5.4 5 1.0 176 83 8.3 8.9 12.6 287.9 105.3 77.7 17 127 7.79 8.38 3.4 1 1 2019 11 Aaron Rodgers GB 36 QB 16 16 13-3-0 353 569 62.0 4002 26 4.6 4 0.7 189 74 7.0 7.6 11.3 250.1 95.4 52.5 36 284 6.15 6.71 6.0 2 3 2019 12 Jimmy Garoppolo SF 28 QB 16 16 13-3-0 329 476 69.1 3978 27 5.7 13 2.7 193 75 8.4 8.3 12.1 248.6 102.0 60.8 36 237 7.31 7.22 7.0 4 4 2019 13 Deshaun Watson HOU 24 QB 15 15 10-5-0 333 495 67.3 3852 26 5.3 12 2.4 191 54 7.8 7.7 11.6 256.8 98.0 70.5 44 257 6.67 6.63 8.2 3 5 2019 14 Baker Mayfield CLE 24 QB 16 16 6-10-0 317 534 59.4 3827 22 4.1 21 3.9 179 89 7.2 6.2 12.1 239.2 78.8 54.4 40 285 6.17 5.29 7.0 1 1 2019 15 Kyler Murray ARI 22 QB 16 16 5-10-1 349 542 64.4 3722 20 3.7 12 2.2 173 88 6.9 6.6 10.7 232.6 87.4 57.7 48 309 5.78 5.55 8.1 1 2 2019 16 Kirk Cousins MIN 31 QB 15 15 10-5-0 307 444 69.1 3603 26 5.9 6 1.4 165 66 8.1 8.7 11.7 240.2 107.4 60.4 28 206 7.2 7.73 5.9 1 1 2019 17 Ryan Fitzpatrick MIA 37 QB 15 13 5-8-0 311 502 62.0 3529 20 4.0 13 2.6 182 51 7.0 6.7 11.3 235.3 85.5 68.3 40 209 6.13 5.78 7.4 3 4 2019 18 Andy Dalton CIN 32 QB 13 13 2-11-0 314 528 59.5 3494 16 3.0 14 2.7 170 66 6.6 6.0 11.1 268.8 78.3 42.1 37 249 5.74 5.19 6.5 0 0 2019 19 Kyle Allen CAR 23 QB 13 12 5-7-0 303 489 62.0 3322 17 3.5 16 3.3 188 52 6.8 6.0 11.0 255.5 80.0 38.3 46 397 5.47 4.76 8.6 0 1 2019 20 Gardner Minshew II JAX 23 QB 14 12 6-6-0 285 470 60.6 3271 21 4.5 6 1.3 150 70 7.0 7.3 11.5 233.6 91.2 44.6 33 184 6.14 6.44 6.6 3 3 2019 21 Mitchell Trubisky CHI 25 QB 15 15 8-7-0 326 516 63.2 3138 17 3.3 10 1.9 156 53 6.1 5.9 9.6 209.2 83.0 41.5 38 234 5.24 5.04 6.9 3 3 2019 22 Lamar Jackson BAL 22 QB 15 15 13-2-0 265 401 66.1 3127 36 9.0 6 1.5 161 83 7.8 8.9 11.8 208.5 113.3 83.0 23 106 7.13 8.19 5.4 1 2 2019 23 Josh Allen BUF 23 QB 16 16 10-6-0 271 461 58.8 3089 20 4.3 9 2.0 146 53 6.7 6.7 11.4 193.1 85.3 49.4 38 237 5.72 5.71 7.6 4 5 2019 24 Daniel Jones NYG 22 QB 13 12 3-9-0 284 459 61.9 3027 24 5.2 12 2.6 140 75 6.6 6.5 10.7 232.8 87.7 55.7 38 295 5.5 5.38 7.6 1 2 2019 25 Sam Darnold NYJ 22 QB 13 13 7-6-0 273 441 61.9 3024 19 4.3 13 2.9 147 92 6.9 6.4 11.1 232.6 84.3 45.6 33 212 5.93 5.5 7.0 2 3 2019 26 Drew Brees NO 40 QB 11 11 8-3-0 281 378 74.3 2979 27 7.1 4 1.1 159 61 7.9 8.8 10.6 270.8 116.3 73.3 12 89 7.41 8.33 3.1 1 2 2019 27 Jacoby Brissett IND 27 QB 15 15 7-8-0 272 447 60

In [0]:
%sql
DROP TABLE IF EXISTS silver_qb_stats_post_2005

In [0]:
qb_silver_post_2005.write.mode('overwrite').saveAsTable('silver_qb_stats_post_2005')

In [0]:
qb_silver_pre_2005 = spark.sql("""
SELECT  
  year
, qb_rank
, (case
    when CHARINDEX("*", player) > 0 then
        left(player, CHARINDEX("*", player) - 1)
    when CHARINDEX("+", player) > 0 then
        left(player, CHARINDEX("+", player) - 1)
    when CHARINDEX("\\\\", player) > 0 then
        left(player, CHARINDEX("\\\\", player) - 1)
    else
        player
  end) as player
, (case when team = "TAM" then "TB"
      when team = "GNB" then "GB"
      when team = "KAN" then "KC"
      when team = "LVR" then "LV"
      when team = "NOR" then "NO"
      when team = "NWE" then "NE"
      when team = "SDG" then "SD"
      when team = "SFO" then "SF"
      else team
  end) as team
, age
, (case         
    when CHARINDEX('Q', position) > 0 then
        'QB'
    when CHARINDEX('q', position) > 0 then
        'QB'
    else
        'non-QB'
    end) as position
, games_played
, games_started
, record
, completions
, attempts
, completion_perc
, yards
, TDs
, TD_perc
, interceptions
, int_perc
, first_down_passes
, longest_throw
, yards_per_attempt
, adj_yards_per_attempt
, yards_per_completion
, yards_per_game
, quarterback_rating
, 0.0 as QBR
, QBR as sacks
, sacks as yards_from_sacks
, net_yards_per_attempt as net_yards_per_attempt
, net_yards_per_attempt as adj_net_yards_per_attempt
, adj_net_yards_per_attempt as sack_percent
, COALESCE(sack_percent, 0) as fourth_qtr_comebacks
, COALESCE(fourth_qtr_comebacks, 0) as game_winning_drives

FROM qb_silver_temp
WHERE player is not null and position is not null 
and (position LIKE '%QB%' or position LIKE '%qb%')
AND year <= 2005 """)

In [0]:
display(qb_silver_pre_2005)

year qb_rank player team age position games_played games_started record completions attempts completion_perc yards TDs TD_perc interceptions int_perc first_down_passes longest_throw yards_per_attempt adj_yards_per_attempt yards_per_completion yards_per_game quarterback_rating QBR sacks yards_from_sacks net_yards_per_attempt adj_net_yards_per_attempt sack_percent fourth_qtr_comebacks game_winning_drives 2005 1 Tom Brady NE 28 QB 16 16 10-6-0 334 530 63.0 4110 26 4.9 14 2.6 197 71 7.8 7.5 12.3 256.9 92.3 0.0 26.0 188 6.86 6.86 4.7 3.0 4 2005 2 Trent Green KC 35 QB 16 16 10-6-0 317 507 62.5 4014 17 3.4 10 2.0 182 60 7.9 7.7 12.7 250.9 90.1 0.0 32.0 204 6.86 6.86 5.9 2.0 3 2005 3 Brett Favre GB 36 QB 16 16 4-12-0 372 607 61.3 3881 20 3.3 29 4.8 202 59 6.4 4.9 10.4 242.6 70.9 0.0 24.0 170 4.45 4.45 3.8 1.0 1 2005 4 Carson Palmer CIN 26 QB 16 16 11-5-0 345 509 67.8 3836 32 6.3 12 2.4 198 70 7.5 7.7 11.1 239.8 101.1 0.0 19.0 105 7.26 7.26 3.6 1.0 3 2005 5 Eli Manning NYG 24 QB 16 16 11-5-0 294 557 52.8 3762 24 4.3 17 3.1 176 78 6.8 6.2 12.8 235.1 75.9 0.0 28.0 184 5.63 5.63 4.8 1.0 2 2005 6 Kerry Collins OAK 33 QB 15 15 4-11-0 302 565 53.5 3759 20 3.5 12 2.1 180 79 6.7 6.4 12.4 250.6 77.3 0.0 39.0 261 5.56 5.56 6.5 1.0 1 2005 7 Peyton Manning IND 29 QB 16 16 14-2-0 305 453 67.3 3747 28 6.2 10 2.2 198 80 8.3 8.5 12.3 234.2 104.1 0.0 17.0 81 8.03 8.03 3.6 1.0 1 2005 8 Drew Bledsoe DAL 33 QB 16 16 9-7-0 300 499 60.1 3639 23 4.6 17 3.4 178 71 7.3 6.7 12.1 227.4 83.7 0.0 49.0 295 5.55 5.55 8.9 4.0 5 2005 9 Drew Brees SD 26 QB 16 16 9-7-0 323 500 64.6 3576 24 4.8 15 3.0 183 54 7.2 6.8 11.1 223.5 89.2 0.0 27.0 223 5.99 5.99 5.1 2.0 2 2005 10 Matt Hasselbeck SEA 30 QB 16 16 13-3-0 294 449 65.5 3459 24 5.3 9 2.0 182 56 7.7 7.9 11.8 216.2 98.2 0.0 24.0 154 7.15 7.15 5.1 2.0 2 2005 11 Jake Delhomme CAR 30 QB 16 16 11-5-0 262 435 60.2 3421 24 5.5 16 3.7 156 80 7.9 7.3 13.1 213.8 88.1 0.0 28.0 214 6.41 6.41 6.0 3.0 3 2005 12 Jake Plummer DEN 31 QB 16 16 13-3-0 277 456 60.7 3366 18 3.9 7 1.5 161 72 7.4 7.5 12.2 210.4 90.2 0.0 22.0 135 6.85 6.85 4.6 1.0 2 2005 13 Steve McNair TEN 32 QB 14 14 4-10-0 292 476 61.3 3161 16 3.4 11 2.3 164 57 6.6 6.3 10.8 225.8 82.4 0.0 20.0 134 5.75 5.75 4.0 0.0 1 2005 14 Mark Brunell WAS 35 QB 16 15 9-6-0 262 454 57.7 3050 23 5.1 10 2.2 155 78 6.7 6.7 11.6 190.6 85.9 0.0 27.0 213 5.92 5.92 5.6 2.0 3 2005 15 Gus Frerotte MIA 34 QB 16 15 9-6-0 257 494 52.0 2996 18 3.6 13 2.6 141 60 6.1 5.6 11.7 187.3 71.9 0.0 26.0 158 5.03 5.03 5.0 0.0 1 2005 16 Aaron Brooks NO 29 QB 13 13 3-10-0 240 431 55.7 2882 13 3.0 17 3.9 145 66 6.7 5.5 12.0 221.7 70.0 0.0 33.0 202 4.69 4.69 7.1 1.0 2 2005 17 Kurt Warner ARI 34 QB 10 10 2-8-0 242 375 64.5 2713 11 2.9 9 2.4 133 63 7.2 6.7 11.2 271.3 85.8 0.0 23.0 158 5.95 5.95 5.8 2.0 2 2005 18 Donovan McNabb PHI 29 QB 9 9 4-5-0 211 357 59.1 2507 16 4.5 9 2.5 116 91 7.0 6.8 11.9 278.6 85.0 0.0 19.0 112 6.14 6.14 5.1 0.0 2 2005 19 David Carr HOU 26 QB 16 16 2-14-0 256 423 60.5 2488 14 3.3 11 2.6 139 53 5.9 5.4 9.7 155.5 77.2 0.0 68.0 424 3.77 3.77 13.8 0.0 1 2005 20 Michael Vick ATL 25 QB 15 15 8-7-0 214 387 55.3 2412 15 3.9 13 3.4 126 58 6.2 5.5 11.3 160.8 73.1 0.0 33.0 201 4.59 4.59 7.9 0.0 1 2005 21 Ben Roethlisberger PIT 23 QB 12 12 9-3-0 168 268 62.7 2385 17 6.3 9 3.4 110 85 8.9 8.7 14.2 198.8 98.6 0.0 23.0 129 7.53 7.53 7.9 2.0 2 2005 22 Trent Dilfer CLE 33 QB 11 11 4-7-0 199 333 59.8 2321 11 3.3 12 3.6 100 80 7.0 6.0 11.7 211.0 76.9 0.0 23.0 139 5.23 5.23 6.5 1.0 1 2005 23 Marc Bulger STL 28 QB 8 8 2-6-0 192 287 66.9 2297 14 4.9 9 3.1 110 57 8.0 7.6 12.0 287.1 94.4 0.0 26.0 188 6.34 6.34 8.3 0.0 1 2005 24 Byron Leftwich JAX 25 QB 11 11 8-3-0 175 302 57.9 2123 15 5.0 5 1.7 101 45 7.0 7.3 12.1 193.0 89.3 0.0 23.0 110 6.42 6.42 7.1 2.0 3 2005 25 Chris Simms TB 25 QB 11 10 6-4-0 191 313 61.0 2035 10 3.2 7 2.2 107 78 6.5 6.1 10.7 185.0 81.4 0.0 29.0 205 5.01 5.01 8.5 3.0 3 2005 26 Joey Harrington DET 27 QB 12 11 4-7-0 188 330 57.0 2021 12 3.6 12 3.6 100 86 6.1 5.2 10.8 168.4 72.0 0.0 24.0 136 4.48 

In [0]:
%sql
show views;

namespace viewName isTemporary qb_silver_temp true

In [0]:
%sql
DROP TABLE IF EXISTS silver_qb_stats_pre_2005

In [0]:
qb_silver_pre_2005.write.mode('overwrite').saveAsTable('silver_qb_stats_pre_2005')

In [0]:
display(draft_picks_silver)

season team round pick_total pro_football_ref_player_id player_name player_id offense_or_defense category position 1980 DET 1 1 SimsBi00 Billy Sims null O RB RB 1980 NYJ 1 2 JoneLa00 Lam Jones null O WR WR 1980 CIN 1 3 MunoAn00 Anthony Munoz null O OL T 1980 GB 1 4 ClarBr23 Bruce Clark null D DL DE 1980 BAL 1 5 DickCu00 Curtis Dickey null O RB RB 1980 LARM 1 6 GreeCu21 Curtis Greer null D DL DE 1980 ATL 1 7 MillJu00 Junior Miller null O TE TE 1980 NYG 1 8 HaynMa00 Mark Haynes null D DB DB 1980 MIN 1 9 MartDo21 Doug Martin null D DL DE 1980 SEA 1 10 GreeJa01 Jacob Green null D DL DE 1980 KC 1 11 BuddBr20 Brad Budde null O OL G 1980 NO 1 12 BrocSt20 Stan Brock null O OL T 1980 SF 1 13 CoopEa00 Earl Cooper null O RB RB 1980 NE 1 14 JameRo20 Roland James null D DB DB 1980 LARD 1 15 WilsMa00 Marc Wilson null O QB QB 1980 BUF 1 16 RitcJi00 Jim Ritcher null O OL G 1980 LARM 1 17 JohnJo23 Johnnie Johnson null D DB DB 1980 WAS 1 18 MonkAr00 Art Monk null O WR WR 1980 CHI 1 19 WilsOt00 Otis Wilson null D LB LB 1980 SF 1 20 StucJi20 Jim Stuckey null D DL DE 1980 MIA 1 21 McNeDo20 Don McNeal null D DB DB 1980 TB 1 22 SnelRa20 Ray Snell null O OL G 1980 PHI 1 23 YounRo00 Roynell Young null D DB DB 1980 BAL 1 24 HatcDe20 Derrick Hatchett null D DB DB 1980 NE 1 25 FergVa00 Vagas Ferguson null O RB RB 1980 GB 1 26 CumbGe20 George Cumby null D LB LB 1980 BAL1 1 27 WhitCh00 Charles White null O RB RB 1980 PIT 1 28 MaloMa00 Mark Malone null O QB QB 1980 BUF 2 29 CribJo00 Joe Cribbs null O RB RB 1980 MIN 2 30 TealWi20 Willie Teal null D DB DB 1980 CIN 2 31 CrisKi20 Kirby Criswell null D LB LB 1980 BAL 2 32 DonaRa00 Ray Donaldson null O OL C 1980 LARM 2 33 MarsDo00 Doug Marsh null O TE TE 1980 GB 2 34 LeexMa20 Mark Lee null D DB DB 1980 PIT 2 35 KohrBo20 Bob Kohrs null D DL DE 1980 ATL 2 36 CurrBu20 Buddy Curry null D LB LB 1980 BUF 2 37 null Gene Bradley null O QB QB 1980 HOU 2 38 FielAn21 Angelo Fields null O OL T 1980 SF 2 39 TurnKe01 Keena Turner null D LB LB 1980 NYJ 2 40 RayxDa20 Darrol Ray null D DB DB 1980 NO 2 41 WaymDa00 Dave Waymer null D DB DB 1980 DEN 2 42 JoneRu00 Rulon Jones null D DL DE 1980 LARD 2 43 MillMa01 Matt Millen null D LB LB 1980 SEA 2 44 HineAn20 Andre Hines null O OL T 1980 NE 2 45 McGrLa20 Larry McGrew null D LB LB 1980 CHI 2 46 SuheMa00 Matt Suhey null O RB RB 1980 NYJ 2 47 ClayRa22 Ralph Clayton null O WR WR 1980 MIA 2 48 StepDw00 Dwight Stephenson null O OL C 1980 TB 2 49 HousKe00 Kevin House null O WR WR 1980 LARM 2 50 PankIr20 Irv Pankey null O OL T 1980 BAL 2 51 FoleTi20 Tim Foley null O OL T 1980 HOU 2 52 SkauDa20 Daryle Skaugstad null D DL NT 1980 PHI 2 53 HarrPe00 Perry Harrington null O RB RB 1980 BAL1 2 54 CrosCl20 Cleveland Crosby null D DL DE 1980 WAS 2 55 MendMa20 Mat Mendenhall null D DL DE 1980 PIT 2 56 GoodJo21 John Goodman null D DL DE 1980 DET 3 57 TurnTo20 Tom Turnure null O OL C 1980 LARM 3 58 ThomJe01 Jewerl Thomas null O RB RB 1980 CIN 3 59 HornRo20 Rod Horn null D DL NT 1980 LARM 3 60 SinnJo20 John Sinnott null O OL T 1980 GB 3 61 KitsSy20 Syd Kitson null O OL G 1980 DET 3 62 FrieMi00 Mike Friede null O WR WR 1980 ATL 3 63 JoneEa20 Earl Jones null D DB DB 1980 NYG 3 64 LapkMy20 Myron Lapka null D DL NT 1980 SF 3 65 MillJi22 Jim Miller null S P P 1980 KC 3 66 HadnJa00 James Hadnot null O RB RB 1980 BUF 3 67 BramMa00 Mark Brammer null O TE TE 1980 MIN 3 68 BoydBr20 Brent Boyd null O OL G 1980 NYJ 3 69 MehlLa00 Lance Mehl null D LB LB 1980 LARM 3 70 IrviLe00 LeRoy Irvin null D DB DB 1980 BUF 3 71 null John Schmeding null O OL G 1980 BAL1 3 72 OdomCl20 Cliff Odom null D LB LB 1980 NE 3 73 McMiSt00 Steve McMichael null D DL DT 1980 DEN 3 74 null Larry Carter null D DB DB 1980 MIA 3 75 BarnBi20 Bill Barnett null D DL DE 1980 TB 3 76 BranSc20 Scot Brantley null D LB LB 1980 SF 3 77 PukiCr20 Craig Puki null D LB LB 1980 DAL 3 78 RoexBi20 Bill Roe null D LB LB 1980 HOU 3 79 SmitTi01 Tim Smith null O WR WR 1980 DAL 3 80 JoneJa01 James Jones null O RB RB 1980 LARM 3 81 BakeCh20 Charles Baker null D LB LB 1

In [0]:
# remove the pro football ref player id, player_id
# filter to quarterbacks in the position
# get rid of category
draft_picks_silver.createOrReplaceTempView("temp_draft_picks")

In [0]:
draft_picks_silver_final = spark.sql("""
select season
, (case when team = "LARM" then "LAR"
       when team = "LA" then "LAR"
       when team = "BAL1" then "CLE"
       when team = "LARD" then "OAK"
      else team
      end) as team
, round
, pick_total
, player_name
, position
from temp_draft_picks

where position ='QB'
""")
display(draft_picks_silver_final)

season team round pick_total player_name position 1980 OAK 1 15 Marc Wilson QB 1980 PIT 1 28 Mark Malone QB 1980 BUF 2 37 Gene Bradley QB 1980 DET 4 85 Eric Hipple QB 1980 LAR 4 89 Rusty Lisch QB 1980 SD 4 101 Ed Luther QB 1980 CLE 4 109 Paul McDonald QB 1980 DAL 5 133 Gary Hogeboom QB 1980 NYG 6 145 Scott Brunner QB 1980 HOU 7 182 Craig Bradshaw QB 1980 BUF 8 202 Todd Krueger QB 1980 MIA 8 214 David Woodley QB 1980 SF 9 237 Dan Hartwig QB 1980 CHI 9 242 Turk Schonert QB 1980 CIN 12 308 Mike Wright QB 1980 NE 12 320 Jimmy Jordan QB 1980 LAR 12 332 Kevin Scanlon QB 1981 GB 1 6 Rich Campbell QB 1981 LAR 2 33 Neil Lomax QB 1981 WAS 4 90 Tom Flick QB 1981 MIA 4 96 Brad Wright QB 1981 DEN 4 98 Mark Herrmann QB 1981 NYG 8 207 Mark Reed QB 1981 MIN 8 210 Wade Wilson QB 1981 TB 9 228 Mike Ford QB 1981 GB 10 255 Nickie Hall QB 1981 WAS 10 257 Phil Kessel QB 1981 CHI 10 260 Tim Clifford QB 1981 PIT 11 292 Rick Trocano QB 1981 NE 11 295 Brian Buckley QB 1981 CIN 12 312 Mark O'Connell QB 1981 KC 12 319 Bob Gagliano QB 1981 SF 12 322 Joe Adams QB 1982 BAL 1 4 Art Schlichter QB 1982 CHI 1 5 Jim McMahon QB 1982 HOU 2 44 Oliver Luck QB 1982 BUF 2 48 Matt Kofler QB 1982 BAL 4 84 Mike Pagel QB 1982 ATL 6 149 Mike Kelley QB 1982 DET 6 154 Mike Machurek QB 1982 BUF 8 218 Luc Tousignant QB 1982 TB 9 242 Bob Lane QB 1982 SF 9 251 Bryan Clark QB 1982 HOU 10 261 Ron Reeves QB 1982 CLE 11 282 Steve Michuta QB 1982 WAS 11 291 Bob Holly QB 1982 NE 11 296 Steve Sandon QB 1982 CIN 12 333 Dan Feraday QB 1983 BAL 1 1 John Elway QB 1983 KC 1 7 Todd Blackledge QB 1983 BUF 1 14 Jim Kelly QB 1983 NE 1 15 Tony Eason QB 1983 NYJ 1 24 Ken O'Brien QB 1983 MIA 1 27 Dan Marino QB 1983 CIN 5 137 Jeff Christensen QB 1983 DAL 6 162 Reggie Collier QB 1983 WAS 6 168 Babe Laufenberg QB 1983 DEN 8 197 Gary Kubiak QB 1983 NE 10 267 Tom Ramsey QB 1983 SD 10 272 Bruce Mathison QB 1983 BAL 11 280 Jim Bob Taylor QB 1983 LAR 12 311 Clete Casper QB 1983 PHI 12 312 David Mangrum QB 1983 OAK 12 333 Scott Lindquist QB 1984 CIN 2 38 Boomer Esiason QB 1984 NYG 3 59 Jeff Hostetler QB 1984 LAR 3 80 Rick McIvor QB 1984 WAS 3 83 Jay Schroeder QB 1984 DAL 5 113 Steve Pelluer QB 1984 MIA 5 138 Dean May QB 1984 ATL 6 148 Ben Bennett QB 1984 GB 6 153 Randy Wright QB 1984 CLE 6 158 Terry Nugent QB 1984 DET 6 160 John Witkowski QB 1984 PIT 7 191 Scott Campbell QB 1984 CHI 9 244 Mark Casale QB 1984 TB 11 281 Blair Kiel QB 1984 LAR 11 296 Kyle Mackey QB 1984 OAK 12 336 Randy Essington QB 1985 PHI 2 37 Randall Cunningham QB 1985 BUF 3 57 Frank Reich QB 1985 MIN 6 142 Steve Bono QB 1985 OAK 6 143 Rusty Hilger QB 1985 SF 6 168 Scott Barry QB 1985 TB 9 232 Steve Calabria QB 1985 SD 9 234 Paul Berner QB 1985 DEN 10 269 Buddy Funck QB 1985 SEA 10 277 John Conner QB 1985 LAR 11 285 Doug Flutie QB 1985 GB 11 294 Joe Shield QB 1986 HOU 1 3 Jim Everett QB 1986 DET 1 12 Chuck Long QB 1986 IND 2 47 Jack Trudeau QB 1986 PIT 3 67 Bubby Brister QB 1986 LAR 3 71 Hugh Millen QB 1986 GB 3 72 Robbie Bosco QB 1986 CIN 4 99 Doug Gaynor QB 1986 WAS 6 146 Mark Rypien QB 1986 DAL 6 150 Stan Gelbaugh QB 1986 CLE 7 174 Mike Norseth QB 1986 MIA 10 274 Jeff Wickersham QB 1986 ATL 11 280 Chris Hegg QB 1986 SEA 11 291 David Norrie QB 1986 LAR 12 312 Kent Austin QB 1986 BUF 12 313 Brian McClure QB 1986 CIN 12 316 Steve Bradley QB 1987 TB 1 1 Vinny Testaverde QB 1987 LAR 1 6 Kelly Stouffer QB 1987 ATL 1 13 Chris Miller QB 1987 CHI 1 26 Jim Harbaugh QB 1987 HOU 3 64 Cody Carlson QB 1987 SD 4 88 Mark Vlasic QB 1987 NE 4 98 Rich Gannon QB 1987 OAK 4 110 Steve Beuerlein QB 1987 DAL 7 180 Kevin Sweeney QB 1987 KC 7 186 Doug Hudson QB 1987 SEA 8 216 Sammy Garza QB 1987 PHI 9 232 Ken Lambiotte QB 1987 GB 10 255 Don Majkowski QB 1987 SF 10 275 John Paye QB 1987 MIN 11 295 Brent Pease QB 1987 NYG 11 307 Dave Walter QB 1987 TB 12 313 Mike Shula QB 1987 MIA 12 322 Jim Karsatos QB 1987 NYJ 12 327 Bill Ransdell QB 1988 PHO 3 68 Tom Tupa QB 1988 IND 3 76 Chris Chandler QB 1988 PHI 6 149 Don McPherson QB 1988 DAL 6 151 Scott Secules QB 1988 WA

In [0]:
%sql
DROP TABLE IF EXISTS silver_draft_picks

In [0]:
draft_picks_silver_final.write.mode('overwrite').saveAsTable("silver_draft_picks")

In [0]:
# only keep the following columns
# game_id, season, week, gameday, away_team, away_score, home_team, home_score, spread_line, away_qb_name, home_qb_name
games_silver.createOrReplaceTempView("games_silver_temp")

In [0]:
games_silver_final = spark.sql("""
select
  game_id
, season
, week
, gameday
, (case when away_team = "LA" then "LAR"
      else away_team
      end) as away_team
, (case when home_team = "LA" then "LAR"
      else home_team
      end) as home_team
, away_score
, home_score
, result_difference_for_home_team
, spread_line
, away_qb_name
, home_qb_name
from games_silver_temp""")
display(games_silver_final)

game_id season week gameday away_team home_team away_score home_score result_difference_for_home_team spread_line away_qb_name home_qb_name 1999_01_MIN_ATL 1999 1 1999-09-12 MIN ATL 17 14 -3 null 00-0003761 00-0002876 1999_01_KC_CHI 1999 1 1999-09-12 KC CHI 17 20 3 null 00-0006300 00-0010560 1999_01_PIT_CLE 1999 1 1999-09-12 PIT CLE 43 0 -43 null 00-0015700 00-0004230 1999_01_OAK_GB 1999 1 1999-09-12 OAK GB 24 28 4 null 00-0005741 00-0005106 1999_01_BUF_IND 1999 1 1999-09-12 BUF IND 14 31 17 null 00-0005363 00-0010346 1999_01_SF_JAX 1999 1 1999-09-12 SF JAX 3 41 38 null 00-0018441 00-0002110 1999_01_CAR_NO 1999 1 1999-09-12 CAR NO 10 19 9 null 00-0001218 00-0007530 1999_01_NE_NYJ 1999 1 1999-09-12 NE NYJ 30 28 -2 null 00-0001361 00-0016193 1999_01_ARI_PHI 1999 1 1999-09-12 ARI PHI 25 24 -1 null 00-0013042 00-0012726 1999_01_DET_SEA 1999 1 1999-09-12 DET SEA 28 20 -8 null 00-0000865 00-0009311 1999_01_BAL_STL 1999 1 1999-09-12 BAL STL 10 27 17 null 00-0011434 00-0017200 1999_01_NYG_TB 1999 1 1999-09-12 NYG TB 17 13 -4 null 00-0006212 00-0004293 1999_01_CIN_TEN 1999 1 1999-09-12 CIN TEN 35 36 1 null 00-0001335 00-0011024 1999_01_DAL_WAS 1999 1 1999-09-12 DAL WAS 41 35 -6 null 00-0000104 00-0008442 1999_01_MIA_DEN 1999 1 1999-09-13 MIA DEN 38 21 -17 null 00-0010379 00-0006423 1999_02_PIT_BAL 1999 2 1999-09-19 PIT BAL 23 20 -3 null 00-0015700 00-0011434 1999_02_NYJ_BUF 1999 2 1999-09-19 NYJ BUF 3 17 14 null 00-0011378 00-0005363 1999_02_JAX_CAR 1999 2 1999-09-19 JAX CAR 22 20 -2 null 00-0002110 00-0001218 1999_02_SEA_CHI 1999 2 1999-09-19 SEA CHI 14 13 -1 null 00-0005379 00-0010560 1999_02_SD_CIN 1999 2 1999-09-19 SD CIN 34 7 -27 null 00-0006808 00-0001335 1999_02_GB_DET 1999 2 1999-09-19 GB DET 15 23 8 null 00-0005106 00-0000865 1999_02_DEN_KC 1999 2 1999-09-19 DEN KC 10 26 16 null 00-0006423 00-0006300 1999_02_ARI_MIA 1999 2 1999-09-19 ARI MIA 16 19 3 null 00-0013042 00-0010379 1999_02_OAK_MIN 1999 2 1999-09-19 OAK MIN 22 17 -5 null 00-0005741 00-0003761 1999_02_IND_NE 1999 2 1999-09-19 IND NE 28 31 3 null 00-0010346 00-0001361 1999_02_WAS_NYG 1999 2 1999-09-19 WAS NYG 50 21 -29 null 00-0008442 00-0006212 1999_02_TB_PHI 1999 2 1999-09-19 TB PHI 19 5 -14 null 00-0004293 00-0012726 1999_02_NO_SF 1999 2 1999-09-19 NO SF 21 28 7 null 00-0007530 00-0018441 1999_02_CLE_TEN 1999 2 1999-09-19 CLE TEN 9 26 17 null 00-0003535 00-0012261 1999_02_ATL_DAL 1999 2 1999-09-20 ATL DAL 7 24 17 null 00-0006299 00-0000104 1999_03_CLE_BAL 1999 3 1999-09-26 CLE BAL 10 17 7 null 00-0003535 00-0002787 1999_03_PHI_BUF 1999 3 1999-09-26 PHI BUF 0 26 26 null 00-0012726 00-0005363 1999_03_CIN_CAR 1999 3 1999-09-26 CIN CAR 3 27 24 null 00-0001335 00-0001218 1999_03_MIN_GB 1999 3 1999-09-26 MIN GB 20 23 3 null 00-0003761 00-0005106 1999_03_TEN_JAX 1999 3 1999-09-26 TEN JAX 20 19 -1 null 00-0012261 00-0002110 1999_03_DET_KC 1999 3 1999-09-26 DET KC 21 31 10 null 00-0000865 00-0006300 1999_03_NYG_NE 1999 3 1999-09-26 NYG NE 14 16 2 null 00-0006212 00-0001361 1999_03_WAS_NYJ 1999 3 1999-09-26 WAS NYJ 27 20 -7 null 00-0008442 00-0011378 1999_03_CHI_OAK 1999 3 1999-09-26 CHI OAK 17 24 7 null 00-0010560 00-0005741 1999_03_SEA_PIT 1999 3 1999-09-26 SEA PIT 29 10 -19 null 00-0009311 00-0015700 1999_03_IND_SD 1999 3 1999-09-26 IND SD 27 19 -8 null 00-0010346 00-0006808 1999_03_ATL_STL 1999 3 1999-09-26 ATL STL 7 35 28 null 00-0002876 00-0017200 1999_03_DEN_TB 1999 3 1999-09-26 DEN TB 10 13 3 null 00-0006423 00-0004293 1999_03_SF_ARI 1999 3 1999-09-27 SF ARI 24 10 -14 null 00-0018441 00-0013042 1999_04_BAL_ATL 1999 4 1999-10-03 BAL ATL 19 13 -6 null 00-0002787 00-0006299 1999_04_NO_CHI 1999 4 1999-10-03 NO CHI 10 14 4 null 00-0007530 00-0010560 1999_04_STL_CIN 1999 4 1999-10-03 STL CIN 38 10 -28 null 00-0017200 00-0001335 1999_04_NE_CLE 1999 4 1999-10-03 NE CLE 19 7 -12 null 00-0001361 00-0003535 1999_04_ARI_DAL 1999 4 1999-10-03 ARI DAL 7 35 28 null 00-0013042 00-0000104 1999_04_NYJ_DEN 1999 4 1999-10-03 NYJ DEN 21 13 -8 null 00-0011378 00-0006423 1999_04_TB_MIN 1999

In [0]:
%sql
DROP TABLE IF EXISTS silver_games_data

In [0]:
games_silver_final.write.mode('overwrite').saveAsTable("silver_games_data")

In [0]:
# get rid of columns tackles, sacks, interceptions
# filter to QB as the position
probowlers_silver.createOrReplaceTempView("probowlers_silver_temp")

In [0]:
probowlers_silver_final = spark.sql("""
select 
  season
, position
, player_name
, (CASE
    WHEN team = "GNB" then "GB"
    WHEN team = "KAN" then "KC"
    WHEN team = "NOR" then "NO"
    WHEN team = "NWE" then "NE"
    WHEN team = "SDG" then "SD"
    when team = "SFO" then "SF"
    when team = "TAM" then "TB"
    else team
   END) as team
, age
, years_pro
, games_played
, starts as games_started
, passing_completions as passes_completed
, passing_attempts as pass_attempts
, passing_yards
, passing_TDs
, passing_interceptions
, rushing_attemps as rush_attempts
, rushing_yards
, rushing_TDs
, all_pro_bool as all_pro
, all_pro_desc
, MVP
, TRUE as probowler
from probowlers_silver_temp
 """)
display(probowlers_silver_final)

season position player_name team age years_pro games_played games_started passes_completed pass_attempts passing_yards passing_TDs passing_interceptions rush_attempts rushing_yards rushing_TDs all_pro all_pro_desc MVP probowler 2019 QB Lamar Jackson BAL 22 1 15 15 265 401 3127 36 6 176 1206 7 true PFW: 1st Tm All-Conf. AP: 1st Tm FW: 1st Tm PFF: 2nd Tm SN: 1st Tm 1 true 2019 QB Russell Wilson SEA 31 7 16 16 341 516 4110 31 5 75 342 3 true PFW: 1st Tm All-Conf. AP: 2nd Tm PFF: 1st Tm 0 true 2019 QB Drew Brees NO 40 18 11 11 281 378 2979 27 4 9 -4 1 false null 0 true 2019 QB Kirk Cousins MIN 31 7 15 15 307 444 3603 26 6 31 63 1 false null 0 true 2019 QB Patrick Mahomes KC 24 2 14 14 319 484 4031 26 5 43 218 2 false null 0 true 2019 QB Aaron Rodgers GB 36 14 16 16 353 569 4002 26 4 46 183 1 false null 0 true 2019 QB Ryan Tannehill TEN 31 7 12 10 201 286 2742 22 6 43 185 4 false null 0 true 2019 QB Deshaun Watson HOU 24 2 15 15 333 495 3852 26 12 82 413 7 false null 0 true 2019 RB Christian McCaffrey CAR 23 2 16 16 0 2 0 0 0 287 1387 15 true PFW: 1st Tm All-Conf. AP: 1st Tm AP: 1st Tm FW: 1st Tm PFF: 2nd Tm SN: 1st Tm 0 true 2019 RB Derrick Henry TEN 25 3 15 15 0 0 0 0 0 303 1540 16 true PFW: 1st Tm All-Conf. AP: 2nd Tm AP: 2nd Tm FW: 1st Tm 0 true 2019 RB Nick Chubb CLE 24 1 16 16 0 0 0 0 0 298 1494 8 true PFW: 1st Tm All-Conf. PFF: 1st Tm 0 true 2019 RB Dalvin Cook MIN 24 2 14 14 0 0 0 0 0 250 1135 13 true PFW: 1st Tm All-Conf. SN: 1st Tm 0 true 2019 RB Ezekiel Elliott DAL 24 3 16 16 0 0 0 0 0 301 1357 12 false null 0 true 2019 RB C.J. Ham MIN 26 2 16 7 0 0 0 0 0 7 17 0 false null 0 true 2019 RB Mark Ingram BAL 30 8 15 15 0 0 0 0 0 202 1018 10 false null 0 true 2019 RB Kyle Juszczyk SF 28 6 12 12 0 0 0 0 0 3 7 0 false null 0 true 2019 RB Alvin Kamara NO 24 2 14 9 1 1 13 0 0 171 797 5 false null 0 true 2019 FB Patrick Ricard BAL 25 2 16 7 0 0 0 0 0 0 0 0 false null 0 true 2019 WR Deonte Harris NO 22 null 14 1 0 0 0 0 0 4 31 0 true PFW: 1st Tm All-Conf. AP: 1st Tm FW: 1st Tm PFF: 1st Tm SN: 1st Tm 0 true 2019 WR Michael Thomas NO 26 3 16 15 0 0 0 0 0 1 -9 0 true PFW: 1st Tm All-Conf. AP: 1st Tm FW: 1st Tm PFF: 1st Tm SN: 1st Tm 0 true 2019 WR Cordarrelle Patterson CHI 28 6 16 4 0 0 0 0 0 17 103 0 true PFW: 1st Tm All-Conf. AP: 1st Tm AP: 2nd Tm FW: 1st Tm SN: 1st Tm 0 true 2019 WR DeAndre Hopkins HOU 27 6 15 15 1 2 6 1 1 2 18 0 true PFW: 1st Tm All-Conf. AP: 1st Tm PFF: 2nd Tm SN: 1st Tm 0 true 2019 WR Julio Jones ATL 30 8 15 15 0 0 0 0 0 2 -3 0 true PFW: 1st Tm All-Conf. AP: 2nd Tm FW: 1st Tm PFF: 1st Tm 0 true 2019 WR Matthew Slater NE 34 11 16 0 0 0 0 0 0 0 0 0 true PFW: 1st Tm All-Conf. AP: 1st Tm FW: 1st Tm PFF: 2nd Tm 0 true 2019 WR Chris Godwin TB 23 2 14 14 0 0 0 0 0 1 8 0 true PFF: 1st Tm AP: 2nd Tm 0 true 2019 WR Mecole Hardman KC 21 null 16 5 0 0 0 0 0 4 17 0 true PFW: 1st Tm All-Conf. AP: 2nd Tm 0 true 2019 WR Keenan Allen LAC 27 6 16 16 0 0 0 0 0 3 16 0 true PFW: 1st Tm All-Conf. 0 true 2019 WR Mike Evans TB 26 5 13 13 0 0 0 0 0 0 0 0 true PFF: 2nd Tm 0 true 2019 WR Andre Roberts BUF 31 9 13 0 0 0 0 0 0 1 7 0 true PFF: 2nd Tm 0 true 2019 WR Davante Adams GB 27 5 12 12 0 0 0 0 0 0 0 0 false null 0 true 2019 WR DJ Chark JAX 23 1 15 14 0 0 0 0 0 2 20 0 false null 0 true 2019 WR Amari Cooper DAL 25 4 16 16 0 0 0 0 0 1 6 0 false null 0 true 2019 WR Kenny Golladay DET 26 2 16 16 0 0 0 0 0 0 0 0 false null 0 true 2019 WR Tyreek Hill KC 25 3 12 12 0 0 0 0 0 8 23 0 false null 0 true 2019 WR Jarvis Landry CLE 27 5 16 16 0 0 0 0 0 1 10 0 false null 0 true 2019 WR Courtland Sutton DEN 24 1 16 14 1 1 38 0 0 3 17 0 false null 0 true 2019 TE George Kittle SF 26 2 14 14 0 0 0 0 0 5 22 0 true PFW: 1st Tm All-Conf. AP: 1st Tm FW: 1st Tm PFF: 1st Tm 0 true 2019 TE Travis Kelce KC 30 6 16 16 0 0 0 0 0 1 4 1 true PFW: 1st Tm All-Conf. AP: 2nd Tm PFF: 2nd Tm SN: 1st Tm 0 true 2019 TE Mark Andrews BAL 24 1 15 4 0 0 0 0 0 0 0 0 false null 0 true 2019 TE Jared Cook NO 32 10 14 7 0 0 0 0 0 0 0 0 false null 0 true 2019 TE Jack Doyle IND 29 6 16

In [0]:
%sql
DROP TABLE IF EXISTS silver_probowlers

In [0]:
probowlers_silver_final.write.mode('overwrite').saveAsTable("silver_probowlers")

In [0]:
display(roster_silver)

season team player_id player_name abbrev_name side_off_def category position games starts years_pro player_value 2006 ARI LeinMa00 Matt Leinart M.Leinart O QB QB 12 11 0 8 2006 ARI LewiJo22 Jonathan Lewis J.Lewis null null null 4 0 0 0 2006 ARI LiwiCh20 Chris Liwienski C.Liwienski O OL LG 16 6 8 4 2006 ARI ArriJ.00 J.J. Arrington J.Arrington null null null 16 0 1 2 2006 ARI LutuDe20 Deuce Lutui D.Lutui O OL RG 15 9 0 5 2006 ARI AyanOb00 Obafemi Ayanbadejo O.Ayanbadejo null null null 14 0 8 1 2006 ARI MackDa20 David Macklin D.Macklin D DB RCB 14 7 6 2 2006 ARI BeisMo20 Monty Beisel M.Beisel D LB MLB 8 2 5 1 2006 ARI MillHa99 Hanik Milligan H.Milligan null null null 16 0 2 1 2006 ARI BergAd00 Adam Bergen A.Bergen O TE TE 14 7 1 1 2006 ARI MoorLa20 Langston Moore L.Moore null null null 3 0 2 0 2006 ARI BerrBe99 Bertrand Berry B.Berry D DL DE 10 10 9 4 2006 ARI OkeaCh20 Chike Okeafor C.Okeafor D DL DE 16 15 7 7 2006 ARI BlacDa20 Darryl Blackstock D.Blackstock D LB LB 16 1 1 1 2006 ARI PaceCa20 Calvin Pace C.Pace D LB LB 16 5 3 3 2006 ARI BoldAn00 Anquan Boldin A.Boldin O WR WR 16 16 3 11 2006 ARI PlaySc20 Scott Player S.Player S P P 16 0 8 2 2006 ARI BronJo00 John Bronson J.Bronson null null null 2 0 1 0 2006 ARI PopeLe00 Leonard Pope L.Pope O TE TE 16 6 0 1 2006 ARI BrowMi21 Milford Brown M.Brown O OL LG 13 12 3 6 2006 ARI rackenei01 Neil Rackers N.Rackers S K K 16 0 6 3 2006 ARI ClanKe20 Kendrick Clancy K.Clancy D DL NT 11 11 6 4 2006 ARI RollAn20 Antrel Rolle A.Rolle D DB LCB 16 16 1 4 2006 ARI CoopCh20 Chris Cooper C.Cooper null null null 13 0 5 1 2006 ARI RossOl20 Oliver Ross O.Ross O OL RT 11 5 8 3 2006 ARI DansKa20 Karlos Dansby K.Dansby D LB LB 14 10 2 5 2006 ARI SchaA.20 A.J. Schable A.Schable null null null 11 0 0 0 2006 ARI DarlJa20 James Darling J.Darling null null null 3 0 9 0 2006 ARI ShipMa00 Marcel Shipp M.Shipp null null null 15 0 5 1 2006 ARI DaviLe21 Leonard Davis L.Davis O OL LT 16 16 5 8 2006 ARI SmitAn22 Antonio Smith A.Smith D DL DE 16 8 2 7 2006 ARI DockDa20 Darnell Dockett D.Dockett D DL DT 16 16 2 7 2006 ARI SpurMi00 Micheal Spurlock M.Spurlock null null null 1 0 0 0 2006 ARI FerrDi00 Diamond Ferri D.Ferri null null null 3 0 0 0 2006 ARI StepAl20 Alex Stepanovich A.Stepanovich O OL C 5 5 2 2 2006 ARI FitzLa00 Larry Fitzgerald L.Fitzgerald O WR WR 13 13 2 8 2006 ARI TateRo00 Robert Tate R.Tate null null null 9 0 9 0 2006 ARI FranAa20 Aaron Francisco A.Francisco D DB FS 16 2 1 2 2006 ARI WakeFr00 Fred Wakefield F.Wakefield O TE TE 16 9 5 0 2006 ARI GreeEr20 Eric Green E.Green D DB RCB 15 8 1 3 2006 ARI WaltTr00 Troy Walters T.Walters O WR WR 15 3 6 2 2006 ARI GrifRo00 Robert Griffith R.Griffith D DB FS 16 16 12 5 2006 ARI WareMa20 Matt Ware M.Ware D DB RCB 14 1 2 1 2006 ARI HayeGe20 Gerald Hayes G.Hayes D LB MLB 14 14 3 7 2006 ARI WarnKu00 Kurt Warner K.Warner O QB QB 6 5 8 5 2006 ARI HodeNa20 Nathan Hodel N.Hodel null null null 16 0 4 1 2006 ARI WatsGa20 Gabe Watson G.Watson D DL NT 12 5 0 3 2006 ARI HoliCa00 Carlyle Holiday C.Holiday O WR WR 4 2 1 0 2006 ARI WellRe20 Reggie Wells R.Wells O OL RT 16 16 3 8 2006 ARI HuffOr20 Orlando Huff O.Huff D LB LB 16 13 5 5 2006 ARI WilsAd99 Adrian Wilson A.Wilson D DB SS 16 16 5 9 2006 ARI HuntDa23 Darrell Hunter D.Hunter null null null 3 0 0 0 2006 ARI JameEd00 Edgerrin James E.James O RB RB 16 16 7 8 2006 ARI JohnBr20 Brandon Johnson B.Johnson null null null 3 0 0 0 2006 ARI JohnBr02 Bryant Johnson B.Johnson O WR WR 16 8 3 6 2006 ARI LeckNi20 Nick Leckey N.Leckey O OL C 14 11 2 5 2006 ATL BeveEr00 Eric Beverly E.Beverly O TE TE 16 2 8 0 2006 ATL MallJo20 Josh Mallard J.Mallard D DL DE 14 1 4 2 2006 ATL BlakDw00 Dwayne Blakley D.Blakley O TE TE 16 4 2 1 2006 ATL MathKe20 Kevin Mathis K.Mathis null null null 8 0 9 1 2006 ATL BoleMi20 Michael Boley M.Boley D LB LB 16 13 1 7 2006 ATL McClTo20 Todd McClure T.McClure O OL C 16 16 6 8 2006 ATL BrooKe00 Keith Brooking K.Brooking D LB LB 16 16 8 8 2006 ATL McCrFr00 Fred McCrary F.McCrary null null null 15 0 11 0 2006 ATL Car

In [0]:
# get rid of following columns:
# player_id, abbrev_name, category, side
roster_silver.createOrReplaceTempView("temp_roster_silver")

In [0]:
roster_silver_final = spark.sql("""
select 
  season
, team
, player_name
, position
, side_off_def
, games
, starts
, years_pro
, player_value
from temp_roster_silver 
where position is not null and side_off_def is not null
""")
display(roster_silver_final)

season team player_name position side_off_def games starts years_pro player_value 2006 ARI Matt Leinart QB O 12 11 0 8 2006 ARI Chris Liwienski LG O 16 6 8 4 2006 ARI Deuce Lutui RG O 15 9 0 5 2006 ARI David Macklin RCB D 14 7 6 2 2006 ARI Monty Beisel MLB D 8 2 5 1 2006 ARI Adam Bergen TE O 14 7 1 1 2006 ARI Bertrand Berry DE D 10 10 9 4 2006 ARI Chike Okeafor DE D 16 15 7 7 2006 ARI Darryl Blackstock LB D 16 1 1 1 2006 ARI Calvin Pace LB D 16 5 3 3 2006 ARI Anquan Boldin WR O 16 16 3 11 2006 ARI Scott Player P S 16 0 8 2 2006 ARI Leonard Pope TE O 16 6 0 1 2006 ARI Milford Brown LG O 13 12 3 6 2006 ARI Neil Rackers K S 16 0 6 3 2006 ARI Kendrick Clancy NT D 11 11 6 4 2006 ARI Antrel Rolle LCB D 16 16 1 4 2006 ARI Oliver Ross RT O 11 5 8 3 2006 ARI Karlos Dansby LB D 14 10 2 5 2006 ARI Leonard Davis LT O 16 16 5 8 2006 ARI Antonio Smith DE D 16 8 2 7 2006 ARI Darnell Dockett DT D 16 16 2 7 2006 ARI Alex Stepanovich C O 5 5 2 2 2006 ARI Larry Fitzgerald WR O 13 13 2 8 2006 ARI Aaron Francisco FS D 16 2 1 2 2006 ARI Fred Wakefield TE O 16 9 5 0 2006 ARI Eric Green RCB D 15 8 1 3 2006 ARI Troy Walters WR O 15 3 6 2 2006 ARI Robert Griffith FS D 16 16 12 5 2006 ARI Matt Ware RCB D 14 1 2 1 2006 ARI Gerald Hayes MLB D 14 14 3 7 2006 ARI Kurt Warner QB O 6 5 8 5 2006 ARI Gabe Watson NT D 12 5 0 3 2006 ARI Carlyle Holiday WR O 4 2 1 0 2006 ARI Reggie Wells RT O 16 16 3 8 2006 ARI Orlando Huff LB D 16 13 5 5 2006 ARI Adrian Wilson SS D 16 16 5 9 2006 ARI Edgerrin James RB O 16 16 7 8 2006 ARI Bryant Johnson WR O 16 8 3 6 2006 ARI Nick Leckey C O 14 11 2 5 2006 ATL Eric Beverly TE O 16 2 8 0 2006 ATL Josh Mallard DE D 14 1 4 2 2006 ATL Dwayne Blakley TE O 16 4 2 1 2006 ATL Michael Boley LB D 16 13 1 7 2006 ATL Todd McClure C O 16 16 6 8 2006 ATL Keith Brooking LB D 16 16 8 8 2006 ATL Paul Carrington DE D 15 2 0 3 2006 ATL Lawyer Milloy SS D 16 16 10 6 2006 ATL Tyson Clabo RG O 10 10 0 5 2006 ATL Roderick Coleman DT D 15 15 7 7 2006 ATL Chris Crocker FS D 16 16 3 7 2006 ATL Alge Crumpler TE O 16 16 5 8 2006 ATL Chauncey Davis DE D 16 13 1 6 2006 ATL Warrick Dunn RB O 16 16 9 9 2006 ATL Allen Rossum CB D 16 6 8 3 2006 ATL Kynan Forney RG O 7 7 5 3 2006 ATL Lance Schulters RCB D 7 1 8 1 2006 ATL Wayne Gandy LT O 16 16 12 8 2006 ATL Darrell Shropshire NT D 13 1 1 1 2006 ATL Justin Griffith FB O 16 11 3 2 2006 ATL DeAngelo Hall LCB D 16 16 2 11 2006 ATL Ed Hartwell MLB D 8 6 5 3 2006 ATL Michael Vick QB O 16 16 5 15 2006 ATL Grady Jackson NT D 16 15 9 6 2006 ATL Jason Webster RCB D 8 7 6 3 2006 ATL Todd Weiner RT O 16 16 8 8 2006 ATL Roddy White WR O 16 5 1 5 2006 ATL Demorrio Williams LB D 16 10 2 6 2006 ATL Michael Jenkins WR O 16 16 2 4 2006 ATL Jimmy Williams RCB D 13 5 0 2 2006 ATL Patrick Kerney DE D 9 9 7 4 2006 ATL John Abraham DE D 8 7 6 3 2006 ATL Michael Koenen P S 16 0 1 0 2006 ATL P.J. Alexander LG O 4 4 2 2 2006 ATL Morten Andersen K S 14 0 24 3 2006 ATL Matt Lehr LG O 11 11 5 5 2006 ATL Jonathan Babineaux DT D 16 1 1 3 2006 ATL Ashley Lelie WR O 15 10 4 4 2006 BAL Samari Rolle RCB D 16 16 8 7 2006 BAL Mike Flynn C O 16 16 8 7 2006 BAL Gerome Sapp SS D 15 1 3 1 2006 BAL Justin Green FB O 12 3 1 0 2006 BAL Bart Scott LB D 16 16 4 15 2006 BAL Kelly Gregg NT D 16 16 7 10 2006 BAL Mike Smith MLB D 8 1 1 1 2006 BAL Todd Heap TE O 16 16 5 7 2006 BAL Matt Stover K S 16 0 15 5 2006 BAL Jarret Johnson DE D 16 2 3 3 2006 BAL Terrell Suggs DE D 16 15 3 13 2006 BAL Quinn Sypniewski TE O 16 3 0 0 2006 BAL Adam Terry LT O 16 2 1 2 2006 BAL Sam Koch P S 16 0 0 2 2006 BAL Adalius Thomas LB D 16 16 6 18 2006 BAL Keydrick Vincent RG O 12 12 5 6 2006 BAL Dawan Landry SS D 16 14 0 7 2006 BAL Daniel Wilcox TE O 14 6 5 2 2006 BAL Jamal Lewis RB O 16 16 6 8 2006 BAL Ray Lewis MLB D 14 14 10 12 2006 BAL Derrick Mason WR O 16 15 9 7 2006 BAL Chris McAlister LCB D 16 16 7 12 2006 BAL Steve McNair QB O 16 16 11 10 2006 BAL Clarence Moore WR O 10 1 2 0 2006 BAL Ovie Mughelli FB O 16 8 3 2 2006 BAL Edwin Mulitalo LG O 4 4 7 2 2006 BAL Justin Bannan DT D 

In [0]:
t = spark.sql("""
select 
distinct 
 team
from temp_roster_silver 
where position is not null and side_off_def is not null
""")
display(t)

team NYJ CAR TB OAK DET TEN BUF BAL LAC NE GB DEN ARI SF KC LAR SEA CIN DAL CLE MIA SD STL MIN ATL PHI WAS NYG PIT NO IND HOU JAX CHI

In [0]:
%sql
DROP TABLE IF EXISTS silver_roster

In [0]:
roster_silver_final.write.mode('overwrite').saveAsTable("silver_roster")

In [0]:
display(standings_silver)

season conference division team wins losses ties winning_percentage division_rank points_scored points_allowed points_differential strength_of_victory strength_of_schedule playoff_seed playoff_outcome 2002 AFC AFC East BUF 8 8 0 0.5 4 379 397 -18 0.351562 0.472656 null null 2002 AFC AFC East MIA 9 7 0 0.5625 3 378 301 77 0.486111 0.507812 null null 2002 AFC AFC East NE 9 7 0 0.5625 2 381 346 35 0.451389 0.523438 null null 2002 AFC AFC East NYJ 9 7 0 0.5625 1 359 336 23 0.5 0.5 4 LostDV 2002 AFC AFC North BAL 7 9 0 0.4375 3 316 354 -38 0.383929 0.5 null null 2002 AFC AFC North CIN 2 14 0 0.125 4 279 456 -177 0.40625 0.53125 null null 2002 AFC AFC North CLE 9 7 0 0.5625 2 344 320 24 0.409722 0.480469 6 LostWC 2002 AFC AFC North PIT 10 5 1 0.65625 1 390 345 45 0.44375 0.484375 3 LostDV 2002 AFC AFC South HOU 4 12 0 0.25 4 213 356 -143 0.484375 0.515625 null null 2002 AFC AFC South IND 10 6 0 0.625 2 349 313 36 0.4 0.476562 5 LostWC 2002 AFC AFC South JAX 6 10 0 0.375 3 328 315 13 0.4375 0.503906 null null 2002 AFC AFC South TEN 11 5 0 0.6875 1 367 324 43 0.471591 0.476562 2 LostCC 2002 AFC AFC West DEN 9 7 0 0.5625 2 392 344 48 0.486111 0.527344 null null 2002 AFC AFC West KC 8 8 0 0.5 4 467 399 68 0.515625 0.527344 null null 2002 AFC AFC West OAK 11 5 0 0.6875 1 450 304 146 0.528409 0.527344 1 LostSB 2002 AFC AFC West SD 8 8 0 0.5 3 333 367 -34 0.453125 0.492188 null null 2002 NFC NFC East DAL 5 11 0 0.3125 4 217 329 -112 0.475 0.5 null null 2002 NFC NFC East NYG 10 6 0 0.625 2 320 279 41 0.45 0.480469 5 LostWC 2002 NFC NFC East PHI 12 4 0 0.75 1 415 241 174 0.432292 0.46875 1 LostCC 2002 NFC NFC East WAS 7 9 0 0.4375 3 307 365 -58 0.4375 0.527344 null null 2002 NFC NFC North CHI 4 12 0 0.25 3 281 379 -98 0.421875 0.519531 null null 2002 NFC NFC North DET 3 13 0 0.1875 4 306 451 -145 0.375 0.492188 null null 2002 NFC NFC North GB 12 4 0 0.75 1 398 328 70 0.411458 0.449219 3 LostWC 2002 NFC NFC North MIN 6 10 0 0.375 2 390 442 -52 0.416667 0.496094 null null 2002 NFC NFC South ATL 9 6 1 0.59375 2 402 314 88 0.416667 0.492188 6 LostDV 2002 NFC NFC South CAR 7 9 0 0.4375 4 258 302 -44 0.357143 0.480469 null null 2002 NFC NFC South NO 9 7 0 0.5625 3 432 388 44 0.5625 0.492188 null null 2002 NFC NFC South TB 12 4 0 0.75 1 346 196 150 0.427083 0.476562 2 WonSB 2002 NFC NFC West ARI 5 11 0 0.3125 4 262 417 -155 0.4 0.5 null null 2002 NFC NFC West SEA 7 9 0 0.4375 3 355 369 -14 0.428571 0.503906 null null 2002 NFC NFC West SF 10 6 0 0.625 1 367 351 16 0.45 0.503906 4 LostDV 2002 NFC NFC West STL 7 9 0 0.4375 2 316 369 -53 0.446429 0.507812 null null 2003 AFC AFC East BUF 6 10 0 0.375 3 243 279 -36 0.4375 0.570312 null null 2003 AFC AFC East MIA 10 6 0 0.625 2 311 261 50 0.3875 0.511719 null null 2003 AFC AFC East NE 14 2 0 0.875 1 348 238 110 0.504464 0.484375 1 WonSB 2003 AFC AFC East NYJ 6 10 0 0.375 4 283 299 -16 0.395833 0.527344 null null 2003 AFC AFC North BAL 10 6 0 0.625 1 391 281 110 0.4 0.457031 4 LostWC 2003 AFC AFC North CIN 8 8 0 0.5 2 346 384 -38 0.46875 0.457031 null null 2003 AFC AFC North CLE 5 11 0 0.3125 4 254 322 -68 0.3625 0.539062 null null 2003 AFC AFC North PIT 6 10 0 0.375 3 300 327 -27 0.364583 0.5 null null 2003 AFC AFC South HOU 5 11 0 0.3125 4 255 380 -125 0.4625 0.570312 null null 2003 AFC AFC South IND 12 4 0 0.75 1 447 336 111 0.447917 0.492188 3 LostCC 2003 AFC AFC South JAX 5 11 0 0.3125 3 276 331 -55 0.45 0.542969 null null 2003 AFC AFC South TEN 12 4 0 0.75 2 435 324 111 0.401042 0.472656 5 LostDV 2003 AFC AFC West DEN 10 6 0 0.625 2 381 301 80 0.40625 0.5 6 LostWC 2003 AFC AFC West KC 13 3 0 0.8125 1 484 332 152 0.384615 0.417969 2 LostDV 2003 AFC AFC West OAK 4 12 0 0.25 3 270 379 -109 0.484375 0.515625 null null 2003 AFC AFC West SD 4 12 0 0.25 4 313 441 -128 0.359375 0.503906 null null 2003 NFC NFC East DAL 10 6 0 0.625 2 289 260 29 0.3875 0.460938 6 LostWC 2003 NFC NFC East NYG 4 12 0 0.25 4 243 387 -144 0.5 0.554688 null null 2003 NFC NFC East PHI 12 4 0 0.75 1 374 287 87 0.4375 0.476562 1 LostC

In [0]:
standings_silver.createOrReplaceTempView("temp_standings_silver")

In [0]:
standings_silver_final = spark.sql("""
select 
season
, (case when team = "LA" then "LAR"
    else team end) as team
, wins
, losses
, SUM(wins) OVER (PARTITION BY team) as alltime_team_wins
, SUM(losses) OVER (PARTITION BY team) as alltime_team_loses
, SUM(wins) OVER (PARTITION BY team ORDER BY season ROWS BETWEEN 1000 PRECEDING AND CURRENT ROW) as rolling_wins
, SUM(losses) OVER (PARTITION BY team ORDER BY season ROWS BETWEEN 1000 PRECEDING AND CURRENT ROW) as rolling_loses
, ties
, winning_percentage
, division_rank
, points_scored
, points_allowed
, points_differential
, strength_of_victory
, strength_of_schedule
, COALESCE(playoff_seed, 100) as playoff_seed
, COALESCE(playoff_outcome, "didn't make it") as playoff_outcome

from temp_standings_silver
""")
display(standings_silver_final)

season team wins losses alltime_team_wins alltime_team_loses rolling_wins rolling_loses ties winning_percentage division_rank points_scored points_allowed points_differential strength_of_victory strength_of_schedule playoff_seed playoff_outcome 2002 ARI 5 11 129 161 5 11 0 0.3125 4 262 417 -155 0.4 0.5 100 didn't make it 2003 ARI 4 12 129 161 9 23 0 0.25 4 225 452 -227 0.53125 0.542969 100 didn't make it 2004 ARI 6 10 129 161 15 33 0 0.375 3 284 322 -38 0.416667 0.460938 100 didn't make it 2005 ARI 5 11 129 161 20 44 0 0.3125 3 311 387 -76 0.3 0.507812 100 didn't make it 2006 ARI 5 11 129 161 25 55 0 0.3125 4 314 389 -75 0.425 0.5 100 didn't make it 2007 ARI 8 8 129 161 33 63 0 0.5 2 404 399 5 0.421875 0.433594 100 didn't make it 2008 ARI 9 7 129 161 42 70 0 0.5625 1 427 426 1 0.368056 0.484375 4 LostSB 2009 ARI 10 6 129 161 52 76 0 0.625 1 375 325 50 0.35625 0.445312 4 LostDV 2010 ARI 5 11 129 161 57 87 0 0.3125 4 289 434 -145 0.45 0.464844 100 didn't make it 2011 ARI 8 8 129 161 65 95 0 0.5 2 312 348 -36 0.390625 0.46875 100 didn't make it 2012 ARI 5 11 129 161 70 106 0 0.3125 4 250 357 -107 0.475 0.550781 100 didn't make it 2013 ARI 10 6 129 161 80 112 0 0.625 3 379 324 55 0.45 0.535156 100 didn't make it 2014 ARI 11 5 129 161 91 117 0 0.6875 2 310 299 11 0.477273 0.523438 5 LostWC 2015 ARI 13 3 129 161 104 120 0 0.8125 1 497 319 178 0.451923 0.472656 2 LostCC 2016 ARI 7 8 129 161 111 128 1 0.46875 2 418 362 56 0.357143 0.457031 100 didn't make it 2017 ARI 8 8 129 161 119 136 0 0.5 3 295 361 -66 0.40625 0.488281 100 didn't make it 2018 ARI 3 13 129 161 122 149 0 0.1875 4 225 425 -200 0.291667 0.523438 100 didn't make it 2019 ARI 5 10 129 161 127 159 1 0.34375 4 361 442 -81 0.375 0.527344 100 didn't make it 2020 ARI 2 2 129 161 129 161 0 0.5 3 98 92 6 0.09375 0.0234375 100 didn't make it 2002 ATL 9 6 153 138 9 6 1 0.59375 2 402 314 88 0.416667 0.492188 6 LostDV 2003 ATL 5 11 153 138 14 17 0 0.3125 4 299 422 -123 0.4625 0.539062 100 didn't make it 2004 ATL 11 5 153 138 25 22 0 0.6875 1 340 337 3 0.431818 0.433594 2 LostCC 2005 ATL 8 8 153 138 33 30 0 0.5 3 351 341 10 0.34375 0.492188 100 didn't make it 2006 ATL 7 9 153 138 40 39 0 0.4375 3 292 328 -36 0.375 0.457031 100 didn't make it 2007 ATL 4 12 153 138 44 51 0 0.25 4 259 414 -155 0.46875 0.515625 100 didn't make it 2008 ATL 11 5 153 138 55 56 0 0.6875 2 391 325 66 0.403409 0.457031 5 LostWC 2009 ATL 9 7 153 138 64 63 0 0.5625 2 363 325 38 0.381944 0.503906 100 didn't make it 2010 ATL 13 3 153 138 77 66 0 0.8125 1 414 288 126 0.4375 0.484375 1 LostDV 2011 ATL 10 6 153 138 87 72 0 0.625 2 402 350 52 0.375 0.480469 5 LostWC 2012 ATL 13 3 153 138 100 75 0 0.8125 1 419 299 120 0.418269 0.421875 1 LostCC 2013 ATL 4 12 153 138 104 87 0 0.25 3 353 443 -90 0.3125 0.550781 100 didn't make it 2014 ATL 6 10 153 138 110 97 0 0.375 3 381 417 -36 0.375 0.476562 100 didn't make it 2015 ATL 8 8 153 138 118 105 0 0.5 2 339 345 -6 0.453125 0.480469 100 didn't make it 2016 ATL 11 5 153 138 129 110 0 0.6875 1 540 406 134 0.448864 0.476562 2 LostSB 2017 ATL 10 6 153 138 139 116 0 0.625 3 353 315 38 0.475 0.542969 6 LostDV 2018 ATL 7 9 153 138 146 125 0 0.4375 2 414 423 -9 0.348214 0.476562 100 didn't make it 2019 ATL 7 9 153 138 153 134 0 0.4375 2 381 399 -18 0.517857 0.542969 100 didn't make it 2020 ATL 0 4 153 138 153 138 0 0.0 4 106 138 -32 0.0 0.0507812 100 didn't make it 2002 BAL 7 9 171 121 7 9 0 0.4375 3 316 354 -38 0.383929 0.5 100 didn't make it 2003 BAL 10 6 171 121 17 15 0 0.625 1 391 281 110 0.4 0.457031 4 LostWC 2004 BAL 9 7 171 121 26 22 0 0.5625 2 317 268 49 0.472222 0.550781 100 didn't make it 2005 BAL 6 10 171 121 32 32 0 0.375 3 265 299 -34 0.375 0.523438 100 didn't make it 2006 BAL 13 3 171 121 45 35 0 0.8125 1 353 201 152 0.447115 0.460938 2 LostDV 2007 BAL 5 11 171 121 50 46 0 0.3125 4 275 384 -109 0.375 0.515625 100 didn't make it 2008 BAL 11 5 171 121 61 51 0 0.6875 2 385 244 141 0.403409 0.515625 6 LostCC 2009 BAL 9 7 171 121 70 58 0 0.5625 2 391 261 130 0.402778 0.5234

In [0]:
%sql
DROP TABLE IF EXISTS silver_standings

In [0]:
standings_silver_final.write.mode('overwrite').saveAsTable("silver_standings")

In [0]:
%sql
show tables;

database tableName isTemporary default silver_draft_picks false default silver_games_data false default silver_probowlers false default silver_qb_stats_post_2005 false default silver_qb_stats_pre_2005 false default silver_roster false default silver_standings false games_silver_temp true probowlers_silver_temp true qb_silver_temp true temp_draft_picks true temp_roster_silver true temp_standings_silver true